<a href="https://colab.research.google.com/github/JamesPeralta/Gymnos/blob/master/NeuralNetwork/Iteration2/Model_Training_GPU.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Gymnos Iteration 2
## Gymnos iteration 2 will use a single stream 2D convolutional neural network. For each video we will be passing in only one frame and the AIs prediction will be based on the single frame.



In [0]:
# You can list all of the hardware device running on your instance
from tensorflow.python.client import device_lib

local_devices = device_lib.list_local_devices()

for device in local_devices:
  print("_______________________________________\n" + str(device))

---
## Mount drive and download libraries from Github

In [0]:
from google.colab import drive
import os
import csv
import importlib
import datetime, os

# Load the TensorBoard notebook extension
!pip install -q tf-nightly-2.0-preview
%load_ext tensorboard

drive.mount('/content/drive')

In [0]:
# Retrieve the Data Generator Library
!curl "https://raw.githubusercontent.com/JamesPeralta/Gymnos/master/NeuralNetwork/Iteration2/GymnosDataGenerator_i2.py?token=AFLRMHIM3FBILWSZXRJKUHC45HRQM" >> GymnosDataGenerator_i2.py
# Retrieve the Helper Functions Library
!curl "https://raw.githubusercontent.com/JamesPeralta/Gymnos/master/NeuralNetwork/Iteration2/HelperFunctions_i2.py?token=AFLRMHMUYT2EXZCEUYWNN4C45GE4W" >> HelperFunctions_i2.py

---
## Imports

In [0]:
import GymnosDataGenerator_i2 as gen
import HelperFunctions_i2 as helper

---
## Create a labels and partitions CSV


In [0]:
csv_location = "/content/drive/My Drive/GYMNOS/Video Dataset/"
labels_location = "/content/drive/My Drive/GYMNOS/Video Dataset/labels.csv"
partitions_location = "/content/drive/My Drive/GYMNOS/Video Dataset/partitions.csv"
ohp_down_reps_location = "/content/drive/My Drive/GYMNOS/Video Dataset/Overhead Press/repetitions/Down/"
ohp_up_reps_location = "/content/drive/My Drive/GYMNOS/Video Dataset/Overhead Press/repetitions/Up/"

ohp_down_label = 0
ohp_up_label = 1

In [0]:
helper.init_labels_csv(labels_location)

In [0]:
# Label the ohp down motion
helper.append_to_labels_csv(labels_location, ohp_down_reps_location, ohp_down_label)

# Label the ohp up motion
helper.append_to_labels_csv(labels_location, ohp_up_reps_location, ohp_up_label)

In [0]:
helper.generate_partitions_csv(partitions_location, labels_location)

---
## Read in the labels and partitions CSVs


In [0]:
partition_location = "/content/drive/My Drive/GYMNOS/Video Dataset/partitions.csv"
labels_location = "/content/drive/My Drive/GYMNOS/Video Dataset/labels.csv"

partition = helper.read_partition_csv(partition_location)
labels = helper.read_labels_csv(labels_location)

In [0]:
print(len(partition["train"]))
print(len(partition["validation"]))
print(len(partition["test"]))

In [0]:
print(partition["train"][1:3])
test_c3d = partition["train"][1:3] 

--- 
## Initialize the DataGenerator

In [0]:
import matplotlib.pyplot as plt

In [0]:
train_params = {'frames_per_video': 16,
                'frame_strides': 6,
                'frame_dim': (112, 112),
                'batch_size': 16,
                'n_classes': 2,
                'shuffle': True}

val_params = {'frames_per_video': 16,
                'frame_strides': 6,
                'frame_dim': (112, 112),
                'batch_size': 3,
                'n_classes': 2,
                'shuffle': True}

train_generator = gen.DataGenerator(partition["train"], labels, **train_params)
val_generator = gen.DataGenerator(partition["validation"], labels, **val_params)

In [0]:
val_generator.__len__()

5

In [0]:
vid_frames, vid_labels = val_generator.__getitem__(3)

In [0]:
print(vid_frames.shape)
print(vid_labels.shape)

In [0]:
print(vid_labels[0])

In [0]:
helper.show_images(vid_frames[0])

---
## Model Imports

In [0]:
import tensorflow as tf
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Conv3D
from tensorflow.keras.layers import MaxPooling3D
from tensorflow.keras.layers import ZeroPadding3D
from tensorflow.keras.layers import Flatten
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Input
from tensorflow.keras.layers import Dropout
from tensorflow.keras import optimizers
from tensorflow.keras.models import load_model

---
## Create the model


In [0]:
# Create C3D Model 
def create_gymnos_model():
    # Recreate the first few layers of the C3D network
    model = Sequential()
    c3d_weights_location = '/content/drive/My Drive/GYMNOS/Product Development/Implementation Details/Gymnos_i2/C3D_Sport1M_weights_keras_2.2.4.h5'
    input_shape = (16, 112, 112, 3)
    # 1st layer group
    model.add(Conv3D(64, (3, 3, 3), activation='relu',
                     padding='same', name='conv1',
                     input_shape=input_shape))
    model.add(MaxPooling3D(pool_size=(1, 2, 2), strides=(1, 2, 2),
                           padding='valid', name='pool1'))
    # 2nd layer group
    model.add(Conv3D(128, (3, 3, 3), activation='relu',
                     padding='same', name='conv2'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool2'))
    # 3rd layer group
    model.add(Conv3D(256, (3, 3, 3), activation='relu',
                     padding='same', name='conv3a'))
    model.add(Conv3D(256, (3, 3, 3), activation='relu',
                     padding='same', name='conv3b'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool3'))
    # 4th layer group
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv4a'))
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv4b'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool4'))
    # 5th layer group
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv5a'))
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv5b'))
    model.add(ZeroPadding3D(padding=((0, 0), (0, 1), (0, 1)), name='zeropad5'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool5'))
    model.add(Flatten())
    # FC layers group
    model.add(Dense(4096, activation='relu', name='fc6'))
    
    model.add(Dense(128, activation='relu'))
    
    model.add(Dense(2, activation='sigmoid'))

    # Load in pre-trained weights
    model.load_weights(c3d_weights_location, by_name=True)
    
    # Freeze first 4 layers
    for layer in model.layers[:-2]:
      layer.trainable = False
      
    model.compile(optimizer=optimizers.RMSprop(lr=0.1), 
                         loss="binary_crossentropy",
                         metrics=['acc'])
    return model

In [0]:
# Create Gymnos model
gymnos_model = create_gymnos_model()

In [0]:
gymnos_model.summary()

In [0]:
# If you stop mid training save it here
mid_training = "/content/drive/My Drive/GYMNOS/Product Development/Implementation Details/Gymnos_i2/gymnos_mid_training.h5"
gymnos_model.save(mid_training)

In [0]:
# Load model that was stopped mid training
gymnos_model = load_model(mid_training)

In [0]:
# Create the tensorBoard callback
logdir = os.path.join("logs", datetime.datetime.now().strftime("%Y%m%d-%H%M%S"))
tensorboard_callback = tf.keras.callbacks.TensorBoard(logdir, histogram_freq=1)

history = gymnos_model.fit_generator(generator=train_generator,
                                     steps_per_epoch=train_generator.__len__(),
                                     epochs=10,
                                     callbacks=[tensorboard_callback],
                                     validation_data=val_generator,
                                     validation_steps=val_generator.__len__())

In [0]:
# Saved the finished model after training
finished_model = "/content/drive/My Drive/GYMNOS/Product Development/Implementation Details/Gymnos_i2/gymnos_finished_i1.h5"
gymnos_model.save(finished_model)

---
## TensorBoard Training Visualization

In [0]:
# Run before you fit the model
%tensorboard --logdir logs

---
## Evaluating the Model
Now that the Model has it's weights initialized, let see how it performs on the test set.

In [0]:
trained_model = load_model(iteration_1_location)

In [0]:
# Parameters
params = {'data_location': "/content/drive/My Drive/GYMNOS/Video Dataset/Frames/",
          'dim': (224, 224, 3),
          'batch_size': 64,
          'n_classes': 2,
          'shuffle': True}

test_generator = gen.DataGenerator(partition["test"], labels, **params)

In [0]:
images, pred_class = test_generator.__getitem__(0)

In [0]:
helper.show_images(images)

In [0]:
model_predictions = trained_model.predict_classes(images)

In [0]:
for index, number in enumerate(model_predictions):
  if number == 0:
    print("Image("+ str(index + 1) + ") is a squat")
  else:
    print("Image("+ str(index + 1) + ") is a overheadpress")